In [1]:
# import requests and beautiful soup for parsing
# run 'pip install requests' or 'pip install bs4' if needed
import requests
import bs4
import json
import pandas
import re
import time

# import required modules and set up environment
import os

# replace file path below with your own local convokit
os.chdir('/Users/marianneaubin/Documents/Classes/CS6742/cs6742-fork')

import convokit
from convokit import Corpus, User, Utterance, Parser
from bs4 import NavigableString

In [2]:
def is_last_page(menu):
    counter = menu.text.replace('Results ', '').replace('to ','').replace('of ','')
    comment_counts = counter.split(' ')
    comment_counts = [i.replace(',','') for i in comment_counts]
    comment_counts = [int(i) for i in comment_counts] 
    if comment_counts[1] == comment_counts[2]:
        return True
    return False

In [3]:
def is_last_thread_page(menu):
    counter = menu.text.replace('Threads ', '').replace('to ','').replace('of ','')
    comment_counts = counter.split(' ')
    comment_counts = [i.replace(',','') for i in comment_counts]
    comment_counts = [int(i) for i in comment_counts] 
    if comment_counts[1] == comment_counts[2]:
        return True
    return False

In [4]:
def get_all_urls(soup,threads):
    threads_info = soup.find_all("div", class_="inner")
    for t in threads_info:
        thread = t.find("a", class_="title")
        title = thread.text
        if title != "Non-partisan PSA: machine guns, full-auto, semi-auto, assault weapons...":
            tid = thread["id"]
            threads[tid] = {}
            url = thread["href"].split('.html')
            threads[tid]["url"] = url[0]
            threads[tid]["title"] = title
            meta_info = str(t.find("span", class_="label").text)
            meta_info = (meta_info.replace("By", '').replace(',','')).strip('\xa0').split('\xa0')
            threads[tid]["op"] = meta_info[0]
            threads[tid]["posted_date"] = meta_info[1]            
    return threads

In [5]:
# threads dict will be the central place to keep information about the thread
# it will be indexed by the title id
# the metadata will be the title, the url for access, the date it was posted, 
# the user who posted it, and how many views it has received
# later, we will add the comment and user metadata to each thread as well

threads = {}

page_num = 1
cont = True
while cont:
    url = 'https://www.debatepolitics.com/gun-control/index' + str(page_num) + '.html'
    resp = requests.get(url)
    soup = bs4.BeautifulSoup(resp.text,'lxml')
    if(is_last_thread_page(soup.find("div", class_="threadpagestats"))):
        cont = False
    page_num = page_num + 1
    threads = get_all_urls(soup, threads)
print(threads)

{'thread_title_375580': {'url': 'https://www.debatepolitics.com/gun-control/375580-wrong-career-choice', 'title': 'Wrong career choice.', 'op': 'Bum', 'posted_date': '11-21-19'}, 'thread_title_375108': {'url': 'https://www.debatepolitics.com/gun-control/375108-gun-home-kills-loved-ones-and-owner', 'title': 'Gun in Home Kills Loved ones and Owner', 'op': 'calamity', 'posted_date': '11-16-19'}, 'thread_title_375950': {'url': 'https://www.debatepolitics.com/gun-control/375950-buffalo-man-shot-leg-victims-dad-pleads-guilty', 'title': "Buffalo man, shot in leg by victim's dad, pleads guilty", 'op': 'Bum', 'posted_date': 'Today'}, 'thread_title_374424': {'url': 'https://www.debatepolitics.com/gun-control/374424-gun-banners-anti-woman', 'title': 'Are Gun banners anti woman?', 'op': 'TurtleDude', 'posted_date': '11-10-19'}, 'thread_title_373457': {'url': 'https://www.debatepolitics.com/gun-control/373457-constitutional-carry-now-effect-oklahoma', 'title': 'Constitutional carry now in effect in

In [6]:
num_threads = len(threads.keys())
print("there are", num_threads, "threads")

there are 449 threads


In [8]:
#init all threads to 0
for k in threads.keys():
    threads[k]['scraped'] = 0

In [10]:
def get_usernames(soup):
    names = []
    names_raw = soup.find_all("a", class_="username online popupctrl")
    names_raw = names_raw + soup.find_all("a", class_="username offline popupctrl")
    for name_raw in names_raw:
        names.append(name_raw.strong.text)
    return names

In [11]:
def extract_username(postinfo):
    name_raw = postinfo.find("a", class_="username offline popupctrl")
    if name_raw is None:
        name_raw = postinfo.find("a", class_="username online popupctrl")
    name = name_raw.strong.text
    return name

In [12]:
def extract_metadata(postinfo):
    jd_raw = postinfo.find("dl", class_="userinfo_extra")
    
    meta = {}
    meta_i = {}
    for i,jd in enumerate(jd_raw):
        if not isinstance(jd, NavigableString):     
            if jd.text == "Join Date":
                meta_i[i+2] = "join_date"
            elif jd.text == "Gender":
                meta_i[i+2] = "gender"
            elif jd.text == "Lean":
                meta_i[i+2] = "lean"
            elif jd.text == "Posts":
                meta_i[i+2] = "posts"
            elif jd.text == "Location":
                meta_i[i+2] = "location"
    for j, jd in enumerate(jd_raw):
        if j in meta_i.keys():
            meta[meta_i[j]] = jd
            
    for elem in meta.keys():
        if elem == "join_date":
            meta[elem] = meta[elem].text
        elif elem == "gender":
            meta[elem] = (meta[elem].find("img")["src"]).replace('https://www.debatepolitics.com/images/misc/','').\
                replace('.gif','')
            if meta[elem] == '':
                meta[elem] = "Unknown"
        elif elem == "lean":
            meta[elem] = meta[elem].text
        elif elem == "posts":
            meta[elem] = int(meta[elem].text.replace(',',''))
        elif elem == "location":
            meta[elem] = meta[elem].text
    
    return meta

In [13]:
def extract_comment(postinfo):
    postedby = postinfo.find("div", class_="bbcode_postedby")
    message = postinfo.find("div", class_="message")
    comment = postinfo.find("blockquote", class_="postcontent restore")
    links = comment.find("a")
    if links != None:
        links.decompose()
    if message != None:
        message.decompose()
    if postedby != None:
        postedby.decompose()
    comment = str(comment.text)
    comment = re.sub('\s\s+', ' ', comment).strip(' ')
    return comment

In [14]:
#import NavigableString

def get_metadata(soup, users_dict, comments_list):
    # meta dict will have a key for each user name
    # the remaining attributes will be in the dict
    # attributes are "join_date", "gender", "lean", "posts", "location", "comment"
    postinfo_list = soup.find_all("div", class_="postdetails")
    
    #for each user
    for postinfo in postinfo_list:
        #extract name of user
        username = extract_username(postinfo)
        #extract metadata
        if username not in users_dict.keys():
            metadata = extract_metadata(postinfo)
            users_dict[username] = {}
            for elem in metadata.keys():
                users_dict[username][elem] = metadata[elem]
        comment = extract_comment(postinfo)
        comments_list.append((username, comment))
    return(users_dict, comments_list)

In [15]:
# this dictionary is the uber dictionary
# each thread title is a key 
# this code is written such that it can be run over and over again
# until it finishes executing

users = {}
counter = 1
num_threads_remaining = 0

for x in threads:
    if threads[x]["scraped"] == 0:
        num_threads_remaining = num_threads_remaining + 1
print(num_threads_remaining, "total threads remaining.")
        
for thread in threads:
    if threads[thread]["scraped"] == 0:
        comments = []
        page_num = 1
        timed_out = 0
        cont = True
        print("starting URL ", counter)
        while cont:
            url = threads[thread]['url'] + str(-page_num) + '.html'
            try:
                resp = requests.get(url, timeout=1)
            except:
                print("timed out")
                timed_out = 1
                threads[thread]["timed_out"] = [page_num]
                continue
            if timed_out == 0:
                soup = bs4.BeautifulSoup(resp.text,'lxml')
                if(is_last_page(soup.find("div", class_="postpagestats"))):
                    cont = False
                page_num = page_num + 1
                users, comments = get_metadata(soup, users, comments)
                #bug bug! needs to be indexed by tid
                threads[thread]["comments"] = comments
        
        #if the thread had no timeouts
        if timed_out == 0:
            #mark that this thread was successfully scraped
            threads[thread]["scraped"] = 1
        print("finished thread ", counter, "out of ", num_threads)
        time.sleep(0.5)
        counter = counter + 1
#print(users)
#print(threads)

starting URL  1
timed out
timed out
finished thread  1 out of  449
starting URL  2
timed out
timed out
finished thread  2 out of  449
starting URL  3
finished thread  3 out of  449
starting URL  4
finished thread  4 out of  449
starting URL  5
timed out
finished thread  5 out of  449
starting URL  6
timed out
finished thread  6 out of  449
starting URL  7
timed out
timed out
finished thread  7 out of  449
starting URL  8
finished thread  8 out of  449
starting URL  9
finished thread  9 out of  449
starting URL  10
finished thread  10 out of  449
starting URL  11
timed out
finished thread  11 out of  449
starting URL  12
finished thread  12 out of  449
starting URL  13
finished thread  13 out of  449
starting URL  14
finished thread  14 out of  449
starting URL  15
finished thread  15 out of  449
starting URL  16
timed out
timed out
timed out
timed out
timed out
finished thread  16 out of  449
starting URL  17
timed out
timed out
timed out
finished thread  17 out of  449
starting URL  1

timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
finished thread  114 out of  449
starting URL  115
finished thread  115 out of  449
starting URL  116
finished thread  116 out of  449
starting URL  117
finished thread  117 out of  449
starting URL  118
finished thread  118 out of  449
starting URL  119
timed out
timed out
finished thread  119 out of  449
starting URL  120
finished thread  120 out of  449
starting URL  121
finished thread  121 out of  449
starting URL  122
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
ti

starting URL  244
timed out
timed out
timed out
finished thread  244 out of  449
starting URL  245
finished thread  245 out of  449
starting URL  246
finished thread  246 out of  449
starting URL  247
finished thread  247 out of  449
starting URL  248
finished thread  248 out of  449
starting URL  249
finished thread  249 out of  449
starting URL  250
finished thread  250 out of  449
starting URL  251
finished thread  251 out of  449
starting URL  252
finished thread  252 out of  449
starting URL  253
timed out
timed out
finished thread  253 out of  449
starting URL  254
timed out
timed out
finished thread  254 out of  449
starting URL  255
finished thread  255 out of  449
starting URL  256
finished thread  256 out of  449
starting URL  257
finished thread  257 out of  449
starting URL  258
timed out
timed out
timed out
timed out
finished thread  258 out of  449
starting URL  259
timed out
finished thread  259 out of  449
starting URL  260
timed out
timed out
timed out
timed out
timed 

timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out


timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out


...

timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out


timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out


timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
finished thread  322 out of  449
starting URL  323
finished thread  323 out of  449
starting URL  324
finished thread  324 out of  449
starting URL  325
finished thread  325 out of  449
starting URL  326
finished thread  326 out of  449
starting URL  327
timed out
timed out
finished thread  327 out of  449
starting URL  328
finished thread  328 out of  449
starting URL  329
timed out
finished thread  329 out of  449
starting URL  330
finished thread  330 out of  449
starting URL  331
finished thread  331 out of  449
starting URL  332
finished thread  332 out of  449
startin

starting URL  438
timed out
finished thread  438 out of  449
starting URL  439
timed out
finished thread  439 out of  449
starting URL  440
timed out
finished thread  440 out of  449
starting URL  441
finished thread  441 out of  449
starting URL  442
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
timed out
finished thread  442 out of  449
starting URL  443
timed out
timed out
finished thread  443 out of  449
starting URL  444
finished thread  444 out of  449
starting URL  445
timed out
finished thread  445 out of  449
starting URL  446
finished thread  446 out of  449
starting URL  447
finished thread  447 out of  449
starting URL  448
finished thread  448 out of  449
starting URL  449
timed out
timed out
finished thread  449 out of  449


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [16]:
# get some basic resulting stats

print("there are", len(threads), "threads")
scraped = 0
for x in threads:
    scraped = scraped + threads[x]["scraped"]
comments = []
for x in threads:
    for y in threads[x]["comments"]:
        comments.append(y)
print("there are", len(comments), "comments")
men = 0
women = 0
unknown = 0

leans = {}

for x in users:
    if "gender" in users[x].keys():
        if users[x]["gender"] == "Male":
             men = men + 1
        elif users[x]["gender"] == "Female":
            women = women + 1
        elif users[x]["gender"] == "Unknown":
            unknown = unknown + 1
    if "lean" in users[x].keys():
        if users[x]["lean"] not in leans.keys():
            leans[users[x]["lean"]] = 0
        leans[users[x]["lean"]] = leans[users[x]["lean"]] + 1
            
print("there are", len(users), "users")
print(men, "men", women, "women", unknown, "unknown")
print(leans)

there are 449 threads
there are 64621 comments
there are 586 users
406 men 45 women 20 unknown
{'Other ': 57, 'Independent ': 86, 'Slightly Liberal ': 23, 'Libertarian ': 32, 'Very Conservative ': 20, 'Undisclosed ': 105, 'Liberal ': 36, 'Moderate ': 19, 'Libertarian - Right ': 16, 'Conservative ': 72, 'Centrist ': 20, 'Private ': 6, 'Progressive ': 27, 'Slightly Conservative ': 15, 'Libertarian - Left ': 9, 'Very Liberal ': 9, 'Socialist ': 14}


# Create corpus

## Users
Each user can be accessed by their name. Additional metadata includes, where available:
    * join date
    * gender
    * lean
    * location
    * posts

In [58]:
## now, we move on to creating the corpus
corpus_users = {k: User(name = k, meta = v) for k,v in users.items()}
#check that this works
print(corpus_users['JoanDavis'].name)
print(corpus_users['JoanDavis'].meta)

#number of users
print("number of users in the data = {}".format(len(corpus_users)))

JoanDavis
{'join_date': 'Nov 2018', 'gender': 'Female', 'lean': 'Undisclosed ', 'posts': 1303}
number of users in the data = 586


## Utterances

In [59]:
utterance_corpus = {}

counter = 1
idx = 1
for th in threads:
    root = idx
    for i,comment in enumerate(threads[th]['comments']):
        reply_to = idx-1
        if reply_to < root:
            reply_to = None
        meta = {'thread_id': th}
        utterance_corpus[idx] = Utterance(idx, corpus_users[comment[0]], root, reply_to, None, comment[1], meta=meta)
        idx += 1

In [60]:
#check this works
print(utterance_corpus[66])

Utterance({'id': 66, 'user': User([('name', 'TurtleDude')]), 'root': 1, 'reply_to': 65, 'timestamp': None, 'text': 'those who commit crimes are not deterred by the existence of a law-only enforcement. gun banners know that-so they want to pass more laws to harass honest people, rather than enforce objectively proper laws that incarcerate criminals', 'meta': {'conversation_id': 'thread_title_375580'}})


In [61]:
utterance_list = [utterance for k,utterance in utterance_corpus.items()]

In [62]:
gun_debate_forum_corpus = Corpus(utterances=utterance_list, version=1)

In [64]:
print("number of conversations in the dataset = {}".format(len(gun_debate_forum_corpus.get_conversation_ids())))

number of conversations in the dataset = 449


In [82]:
print(threads['thread_title_375580'])

{'url': 'https://www.debatepolitics.com/gun-control/375580-wrong-career-choice', 'title': 'Wrong career choice.', 'op': 'Bum', 'posted_date': '11-21-19', 'scraped': 1, 'comments': [('Bum', "Should have gone to a trade school; Robbery suspect shot dead with own gun by homeowner, police say it happened shortly before 3 p.m. Tuesday at 5822 Ludington Dr., near Hillcroft and W. Bellfort Avenue.\nPolice say the homeowner was in his garage when the suspect approached him and said it was a robbery. That's when police say the homeowner managed to get the suspect's gun and shot him. And, one individual pursuing a career in crime failed his thug final exams: Beauty store clerk shoots, kills masked suspect during attempted armed robbery; AKRON, Ohio — A pair of masked men tried to rob a beauty shop but were met with gunfire, according to WJW. Friday evening, officers responded to Royal Beauty Supply Store on the 900 block of South Arlington Street in Akron, Ohio.\nPolice say two masked men, armed

In [86]:
## add conversation meta data

for conv_id in gun_debate_forum_corpus.conversations:
    conv = gun_debate_forum_corpus.get_conversation(conv_id)
    for first in conv.get_utterance_ids():
        tid = conv.get_utterance(first).meta['conversation_id']
        break
    meta = {
        'thread_id': tid,
        'url': threads[tid]['url'],
        'title': threads[tid]['title'],
        'op': threads[tid]['op'],
        'posted_date': threads[tid]['posted_date']
    }
    conv.meta=meta

In [88]:
## save corpus
gun_debate_forum_corpus.print_summary_stats()
gun_debate_forum_corpus.dump("gun_debate_forum_corpus", base_path='./datasets/gun_debate_forum_corpus/' )

Number of Users: 586
Number of Utterances: 64621
Number of Conversations: 449


FileNotFoundError: [Errno 2] No such file or directory: './datasets/gun_debate_forum_corpus/gun_debate_forum_corpus'